In [1]:
# Importation des librairies

import numpy as np
import pandas as pd
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

from sklearn.model_selection import train_test_split
from lazypredict.Supervised import LazyRegressor
from sklearn.utils import all_estimators
from sklearn.base import RegressorMixin
from imblearn.under_sampling import RandomUnderSampler
from sklearn.preprocessing import KBinsDiscretizer
import time


# Ajuster les paramètres pour afficher toutes les lignes et colonnes

pd.set_option("display.max_rows", None)
pd.set_option("display.max_columns", None)

In [2]:
from collections import Counter


# Définition des variables cibles et des variables explicatives pour l'analyse des temps d'intervention
cols_cible_type = ["TurnoutTimeSeconds", "TravelTimeSeconds", "PumpSecondsOnSite"]
cols_Data = [
    ["CalYear", "HourOfCall", "Postcode_district", "Month", "DayOfWeek"],
    ["CalYear", "HourOfCall", "Postcode_district", "Month", "DayOfWeek"],
    ["CalYear", "PropertyType", "StopCode"],
]
cols_cible = [
    ["TurnoutTimeSeconds_min", "TurnoutTimeSeconds_mean", "TurnoutTimeSeconds_max"],
    ["TravelTimeSeconds_min", "TravelTimeSeconds_mean", "TravelTimeSeconds_max"],
    ["PumpSecondsOnSite_min", "PumpSecondsOnSite_mean", "PumpSecondsOnSite_max"]
    # NumPumpsAttending??
]

def load_df(col_cible_type):
    
    """
    Cette fonction charge un fichier CSV contenant un DataFrame et le retourne.

    Paramètres :

            col_cible_type (str): Chaîne de caractères utilisée pour construire le nom du fichier à charger. Le fichier attendu est nommé _df_ready_{col_cible_type}.csv et se trouve dans le répertoire ../data/.
    
    Retour :

           Le DataFrame chargé depuis le fichier CSV.

    """
    
    df = pd.read_csv(f"../data/_df_ready_{col_cible_type}.csv", sep=";", low_memory=False)
    
    return df

def load_df_full(col_cible_type):
    
    """
    Cette fonction charge un fichier CSV contenant un DataFrame et le retourne.

    Paramètres :

            col_cible_type (str): Chaîne de caractères utilisée pour construire le nom du fichier à charger. Le fichier attendu est nommé _df_ready_{col_cible_type}.csv et se trouve dans le répertoire ../data/.
    
    Retourne :

           Le DataFrame chargé depuis le fichier CSV.

    """
    
    df = pd.read_csv(
        f"../data/_df_ready_full_{col_cible_type}.csv", sep=";", low_memory=False
    )
    # Contrôle
    # display(df.head(3))
    # display(df.info())
    return df

def Create_X(df_limited, index):    
    
    """
    Crée une matrice de caractéristiques X à partir d'un DataFrame en excluant certaines colonnes cibles.

    Paramètres :
    ------------
    df_limited : pd.DataFrame
        Le DataFrame contenant les données à filtrer.
    index : int
        Un indice permettant de sélectionner les colonnes explicatives à conserver à partir de la liste `cols_Data`.

    Retourne :
    ----------
    X : pd.DataFrame
        Un DataFrame contenant uniquement les colonnes explicatives sélectionnées.

    Fonctionnement :
    ----------------
    1. Affiche les dimensions initiales du DataFrame.
    2. Supprime les colonnes cibles définies dans `cols_cible` ainsi que `"NumPumpsAttending"`.
    3. Sélectionne uniquement les colonnes contenant certaines sous-chaînes définies dans `cols_Data[index]`.
    4. Affiche un aperçu des données transformées et leurs nouvelles dimensions.
    5. Retourne le DataFrame `X` contenant uniquement les colonnes explicatives filtrées.
    """
    
    print(df_limited.shape)
    # Crée X sans les target
    cols_to_remove = [item for sublist in cols_cible for item in sublist] + [
        "NumPumpsAttending"
    ]
    print("cols_to_remove", cols_to_remove)
    X = df_limited.drop(cols_to_remove, axis=1)
    # Ne conserve que certaines colonnes explicatives
    # Crée une liste des colonnes à conserver
    cols_to_keep = [
        col
        for col in X.columns
        if any(substring in col for substring in cols_Data[index])
    ]
    print("cols_to_keep", cols_to_keep)
    # Conserver uniquement ces colonnes
    X = X[cols_to_keep]

    display(X.head(2))
    print(X.shape)
    return X



In [9]:
# ------------------------------------- Lazy predict 


# Définition des listes de variables cibles 

cols_cible_filter = [
    "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    "PumpSecondsOnSite_mean",
]


# Définition des modèles à exclure
ignore_regressors = [
    "ExtraTreesRegressor",
    "NuSVR",
    "QuantileRegressor",
    "SVR",
    "CCA",
    "GammaRegressor",
    "GaussianProcessRegressor",
    "IsotonicRegression",
    "MultiOutputRegressor",
    "MultiTaskElasticNet",
    "MultiTaskElasticNetCV",
    "MultiTaskLasso",
    "MultiTaskLassoCV",
    "PLSCanonical",
    "RadiusNeighborsRegressor",
    "RegressorChain",
    "StackingRegressor",
    "KernelRidge",
    "ARDRegression",
    "TweedieRegressor",
]


# Création d'une liste contenant les modèles de régression disponible dans scikit-learn, tout en excluant ceux de la liste "ignore_regressors"
REGRESSORS = [
    estimator
    for estimator in all_estimators()
    if (
        issubclass(estimator[1], RegressorMixin)
        and (not (estimator[0] in ignore_regressors))
    )
]

all_results = pd.DataFrame()


# Pour chaque colonne cible, chargement du DataFrame correspondant en appelant la fonction load_df(name)
for index, name in enumerate(cols_cible_type):
    df = load_df(name)
    # Itèration sur différentes années à partir de 2021
    # Pour chaque année, on conserve que les lignes où la colonne CalYear est supérieure ou égale à l'année de départ (year_floor)
    for year_floor in range(13, 16):
        print("-----------------------------------------------------")
        print("year", 2024 - 16 + year_floor)
        print("-----------------------------------------------------")
        df_limited = df[df.CalYear >= year_floor]  # >= 2021

        # Création des variables explicatives X (les features) à partir du DataFrame df_limited. 
        # La fonction prend un paramètre index qui permet de spécifier quelles colonnes sont utilisées pour X.
        X = Create_X(df_limited, index)

        # pour chaque colonne cible dans cols_cible[index], le code vérifie si elle fait partie de la liste cols_cible_filter. 
        # Si ce n'est pas le cas, il passe à la colonne suivante.
        for col_cible in cols_cible[index]:
            if not(col_cible in cols_cible_filter):
                continue
            print("cible", col_cible)
            # Définition de la variable cible y, la colonne que l'on veut prédire à partir des variables explicatives X.
            y = df_limited[col_cible]
            X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
            # Réchantillonne
            # X_train_samp, y_train_samp = custom_random_undersampler(X_train, y_train)
            X_train_samp, y_train_samp = X_train, y_train
            # LazyPredict
            myREGRESSORS = REGRESSORS
            print(myREGRESSORS)
            # myREGRESSORS = myREGRESSORS[4:6]
            reg = LazyRegressor(
                verbose=2,
                ignore_warnings=False,
                custom_metric=None,
                regressors=myREGRESSORS,
            )
            models, predictions = reg.fit(X_train_samp, X_test, y_train_samp, y_test)
            # models, predictions = reg.fit(X_train, X_test, y_train, y_test)
            # Ajoute le nom de la colonne
            models["Target"] = col_cible
            models["Year floor"] = 2024 - 16 + year_floor
            # Concaténe dans les résultats
            all_results = pd.concat([all_results, models], axis=0)
            display(models)
            models.to_csv(f"../data/_autoML_regressor_{col_cible}.csv", sep=";", index=True)
            # break
        # break

# Tri des résultats et exportation dans un fichier CSV        
all_results = all_results.sort_values(by=["Target", "RMSE"], ascending=[False, True])
all_results.to_csv(f"../data/_autoML_regressor.csv", sep=";", index=True)


-----------------------------------------------------
year 2021
-----------------------------------------------------
(444247, 42)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Postcode_district_0', 'Postcode_district_1', 'Postcode_district_2', 'Postcode_district_3', 'Postcode_district_4', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1147280       13             0             0             0             0   
1147281       13             0             0             0             0   

         HourOfCall_4  Postcode_district_0  Postcode_district_1  \
1147280             1                    0                    0   
1147281             1                    0                    0   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1147280                    0                    0                    1   
1147281                    0                    0                    1   

         Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  \
1147280        0        0        0        1            0            1   
1147281        0        0        0        1            0            1   

         DayOfWeek_2  
1147280            0  
1147281            0

(444247, 18)
cible TurnoutTimeSeconds_mean
[('AdaBoostRegressor', <class 'sklearn.ensemble._weight_boosting.AdaBoostRegressor'>), ('BaggingRegressor', <class 'sklearn.ensemble._bagging.BaggingRegressor'>), ('BayesianRidge', <class 'sklearn.linear_model._bayes.BayesianRidge'>), ('DecisionTreeRegressor', <class 'sklearn.tree._classes.DecisionTreeRegressor'>), ('DummyRegressor', <class 'sklearn.dummy.DummyRegressor'>), ('ElasticNet', <class 'sklearn.linear_model._coordinate_descent.ElasticNet'>), ('ElasticNetCV', <class 'sklearn.linear_model._coordinate_descent.ElasticNetCV'>), ('ExtraTreeRegressor', <class 'sklearn.tree._classes.ExtraTreeRegressor'>), ('GradientBoostingRegressor', <class 'sklearn.ensemble._gb.GradientBoostingRegressor'>), ('HistGradientBoostingRegressor', <class 'sklearn.ensemble._hist_gradient_boosting.gradient_boosting.HistGradientBoostingRegressor'>), ('HuberRegressor', <class 'sklearn.linear_model._huber.HuberRegressor'>), ('KNeighborsRegressor', <class 'sklearn.neig

  3%|▎         | 1/35 [00:05<02:54,  5.14s/it]

{'Model': 'AdaBoostRegressor', 'R-Squared': 0.11130882084114446, 'Adjusted R-Squared': 0.11112874360206282, 'RMSE': np.float64(34.86080349122066), 'Time taken': 5.1385064125061035}


...

 91%|█████████▏| 32/35 [04:59<00:07,  2.49s/it]

{'Model': 'SGDRegressor', 'R-Squared': 0.13908706751844058, 'Adjusted R-Squared': 0.13883831511529643, 'RMSE': np.float64(1353.5571676547406), 'Time taken': 0.6104817390441895}


100%|██████████| 35/35 [05:37<00:00,  9.65s/it]

{'Model': 'TheilSenRegressor', 'R-Squared': 0.003514966166231037, 'Adjusted R-Squared': 0.0032270415254095353, 'RMSE': np.float64(1456.2380593240218), 'Time taken': 37.67497777938843}
{'Model': 'TransformedTargetRegressor', 'R-Squared': 0.13962181023631026, 'Adjusted R-Squared': 0.13937321234186395, 'RMSE': np.float64(1353.1367318352352), 'Time taken': 0.18442201614379883}
VotingRegressor model failed to execute
VotingRegressor.__init__() missing 1 required positional argument: 'estimators'


Adjusted R-Squared  R-Squared    RMSE  \
Model                                                                  
RandomForestRegressor                        0.22       0.22 1288.40   
HistGradientBoostingRegressor                0.22       0.22 1288.52   
BaggingRegressor                             0.22       0.22 1288.90   
MLPRegressor                                 0.22       0.22 1288.91   
DecisionTreeRegressor                        0.22       0.22 1289.21   
ExtraTreeRegressor                           0.22       0.22 1289.89   
GradientBoostingRegressor                    0.21       0.21 1293.53   
AdaBoostRegressor                            0.16       0.16 1335.07   
BayesianRidge                                0.14       0.14 1353.14   
RidgeCV                                      0.14       0.14 1353.14   
Ridge                                        0.14       0.14 1353.14   
LassoLarsCV                                  0.14       0.14 1353.14   
Lars                                         0.14       0.14 1353.14   
LassoLarsIC                                  0.14       0.14 1353.14   
LarsCV                                       0.14       0.14 1353.14   
TransformedTargetRegressor                   0.14       0.14 1353.14   
LinearRegression                             0.14       0.14 1353.14   
LassoCV                                      0.14       0.14 1353.15   
LassoLars                                    0.14       0.14 1353.17   
Lasso                                        0.14       0.14 1353.17   
SGDRegressor                                 0.14       0.14 1353.56   
PLSRegression                                0.13       0.13 1357.14   
OrthogonalMatchingPursuitCV                  0.13       0.13 1358.08   
ElasticNetCV                                 0.13       0.13 1361.53   
ElasticNet                                   0.13       0.13 1362.58   
PoissonRegressor                             0.12       0.12 1367.47   
OrthogonalMatchingPursuit                    0.10       0.10 1386.42   
KNeighborsRegressor                          0.07       0.07 1403.43   
HuberRegressor                               0.06       0.06 1411.04   
PassiveAggressiveRegressor                   0.05       0.05 1420.85   
LinearSVR                                    0.05       0.05 1424.23   
TheilSenRegressor                            0.00       0.00 1456.24   
DummyRegressor                              -0.00      -0.00 1458.85   
RANSACRegressor                             -0.07      -0.07 1507.49   

                               Time Taken                  Target  Year floor  
Model                                                                          
RandomForestRegressor                6.53  PumpSecondsOnSite_mean        2023  
HistGradientBoostingRegressor        0.48  PumpSecondsOnSite_mean        2023  
BaggingRegressor                     0.86  PumpSecondsOnSite_mean        2023  
MLPRegressor                       129.80  PumpSecondsOnSite_mean        2023  
DecisionTreeRegressor                0.22  PumpSecondsOnSite_mean        2023  
ExtraTreeRegressor                   0.24  PumpSecondsOnSite_mean        2023  
GradientBoostingRegressor            4.58  PumpSecondsOnSite_mean        2023  
AdaBoostRegressor                    1.09  PumpSecondsOnSite_mean        2023  
BayesianRidge                        0.23  PumpSecondsOnSite_mean        2023  
RidgeCV                              0.30  PumpSecondsOnSite_mean        2023  
Ridge                                0.09  PumpSecondsOnSite_mean        2023  
LassoLarsCV                          0.47  PumpSecondsOnSite_mean        2023  
Lars                                 0.10  PumpSecondsOnSite_mean        2023  
LassoLarsIC                          0.24  PumpSecondsOnSite_mean        2023  
LarsCV                               0.46  PumpSecondsOnSite_mean        2023  
TransformedTargetRegressor           0.18  PumpSecondsOnSite_mean        2023 

In [19]:
# ------------------------------------- Lazy predict par code postal

# # Définition des listes de variables cibles 
cols_cible_filter = [
    # "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    # "PumpSecondsOnSite_mean",
]

# # Définition des modèles à exclure
ignore_regressors = [
    "ExtraTreesRegressor",
    "NuSVR",
    "QuantileRegressor",
    "SVR",
    "CCA",
    "GammaRegressor",
    "GaussianProcessRegressor",
    "IsotonicRegression",
    "MultiOutputRegressor",
    "MultiTaskElasticNet",
    "MultiTaskElasticNetCV",
    "MultiTaskLasso",
    "MultiTaskLassoCV",
    "PLSCanonical",
    "RadiusNeighborsRegressor",
    "RegressorChain",
    "StackingRegressor",
    "KernelRidge",
    "ARDRegression",
    "TweedieRegressor",
]

# Création d'une liste contenant les modèles de régression disponible dans scikit-learn, tout en excluant ceux de la liste "ignore_regressors"
REGRESSORS = [
    estimator
    for estimator in all_estimators()
    if (
        issubclass(estimator[1], RegressorMixin)
        and (not (estimator[0] in ignore_regressors))
    )
]

all_results = pd.DataFrame()

# Pour chaque colonne cible, chargement du DataFrame correspondant en appelant la fonction load_df(name)
for index, name in enumerate(cols_cible_type):
    df = load_df_full(name)
    # Itèration sur différentes années à partir de 2013 jusqu'à 2015
    # Pour chaque année, on conserve que les lignes où la colonne CalYear est supérieure ou égale à l'année de départ (year_floor)
    for year_floor in range(13, 16): 
        df_limited = df[df.CalYear >= year_floor]  # >= 2021
        print("-----------------------------------------------------")
        print("year", 2024 - 16 + year_floor)
        print("-----------------------------------------------------")

        for col_cible in cols_cible[index]:
            if not (col_cible in cols_cible_filter):
                continue
            print("cible", col_cible)

            # boucle par CP
            # Obtenez les valeurs uniques des codes postaux
            unique_postcodes = df_limited["Postcode_district"].unique()
            # Parcours de chaque code postal
            limiter = 0
            for postcode in unique_postcodes:
                # Limite pour test
                limiter += 1 
                # if limiter > 4:
                #     break
                # Filtre par postcode et supprime la colonne
                df_postcode = df_limited[df_limited["Postcode_district"] == postcode]
                df_postcode = df_postcode.drop(columns=["Postcode_district"])
                if len(df_postcode) < 5:
                    continue
                # Crée X et y
                X = Create_X(df_postcode, index)
                print("Postcode_district", postcode, X.shape)
                # display(X.head())
                y = df_postcode[col_cible]
                X_train, X_test, y_train, y_test = train_test_split(
                    X, y, test_size=0.2, random_state=42
                )
                # Réchantillonne
                # X_train_samp, y_train_samp = custom_random_undersampler(X_train, y_train)
                X_train_samp, y_train_samp = X_train, y_train
                # LazyPredict
                myREGRESSORS = REGRESSORS
                print(myREGRESSORS)
                # myREGRESSORS = myREGRESSORS[4:6]
                reg = LazyRegressor(
                    verbose=0,
                    ignore_warnings=False,
                    custom_metric=None,
                    regressors=myREGRESSORS,
                )
                models, predictions = reg.fit(X_train_samp, X_test, y_train_samp, y_test)
                # models, predictions = reg.fit(X_train, X_test, y_train, y_test)
                # Ajoute le nom de la colonne
                models["Target"] = col_cible
                models["Postcode_district"] = postcode
                models["Year floor"] = 2024 - 16 + year_floor
                # Concaténe dans les résultats
                all_results = pd.concat([all_results, models], axis=0)
                # display(models)
                # models.to_csv(
                #     f"../data/_autoML_regressor_{col_cible}.csv", sep=";", index=True
                # )
                # break
            # break
all_results = all_results.sort_values(by=["Target", "Postcode_district", "RMSE"], ascending=True)
all_results.to_csv(
    f"../data/_autoML_regressor by postcode detailled.csv", sep=";", index=False
)

# Calculer les statistiques par modèle
summary_df = (
    all_results.groupby(["Target", "Year floor", "Model"])
    .agg(
        RMSE_Mean=("RMSE", "mean"),
        RMSE_Min=("RMSE", "min"),
        RMSE_Max=("RMSE", "max"),
    )
    .reset_index()
)
summary_df = summary_df.sort_values(by=["Target", "RMSE_Mean"], ascending=True)

# all_results = all_results.sort_values(by=["Target", "F1 Score"], ascending=False)
summary_df.to_csv(f"../data/_autoML_regressor by postcode.csv", sep=";", index=False)

-----------------------------------------------------
year 2021
-----------------------------------------------------
-----------------------------------------------------
year 2022
-----------------------------------------------------
-----------------------------------------------------
year 2023
-----------------------------------------------------
-----------------------------------------------------
year 2021
-----------------------------------------------------
cible TravelTimeSeconds_mean
(861, 37)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1147280       13             0             0             0             0   
1147847       13             0             0             1             0   

         HourOfCall_4  Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  \
1147280             1        0        0        0        1            0   
1147847             0        0        0        0        1            1   

         DayOfWeek_1  DayOfWeek_2  
1147280            1            0  
1147847            0            0

(861, 13)
Postcode_district N10 (861, 13)
[('AdaBoostRegressor', <class 'sklearn.ensemble._weight_boosting.AdaBoostRegressor'>), ('BaggingRegressor', <class 'sklearn.ensemble._bagging.BaggingRegressor'>), ('BayesianRidge', <class 'sklearn.linear_model._bayes.BayesianRidge'>), ('DecisionTreeRegressor', <class 'sklearn.tree._classes.DecisionTreeRegressor'>), ('DummyRegressor', <class 'sklearn.dummy.DummyRegressor'>), ('ElasticNet', <class 'sklearn.linear_model._coordinate_descent.ElasticNet'>), ('ElasticNetCV', <class 'sklearn.linear_model._coordinate_descent.ElasticNetCV'>), ('ExtraTreeRegressor', <class 'sklearn.tree._classes.ExtraTreeRegressor'>), ('GradientBoostingRegressor', <class 'sklearn.ensemble._gb.GradientBoostingRegressor'>), ('HistGradientBoostingRegressor', <class 'sklearn.ensemble._hist_gradient_boosting.gradient_boosting.HistGradientBoostingRegressor'>), ('HuberRegressor', <class 'sklearn.linear_model._huber.HuberRegressor'>), ('KNeighborsRegressor', <class 'sklearn.neigh

100%|██████████| 35/35 [00:03<00:00, 10.55it/s]

VotingRegressor model failed to execute
VotingRegressor.__init__() missing 1 required positional argument: 'estimators'
(1327, 37)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


...

KNeighborsRegressor model failed to execute
Expected n_neighbors <= n_samples_fit, but n_neighbors = 5, n_samples_fit = 4, n_samples = 2
LarsCV model failed to execute
Cannot have number of splits n_splits=5 greater than the number of samples: n_samples=4.
LassoCV model failed to execute
Cannot have number of splits n_splits=5 greater than the number of samples: n_samples=4.


 63%|██████▎   | 22/35 [00:00<00:00, 51.11it/s]

LassoLarsCV model failed to execute
Cannot have number of splits n_splits=5 greater than the number of samples: n_samples=4.
LassoLarsIC model failed to execute
You are using LassoLarsIC in the case where the number of samples is smaller than the number of features. In this setting, getting a good estimate for the variance of the noise is not possible. Provide an estimate of the noise variance in the constructor.
OrthogonalMatchingPursuitCV model failed to execute
Cannot have number of splits n_splits=5 greater than the number of samples: n_samples=4.
RANSACRegressor model failed to execute
`min_samples` may not be larger than number of samples: n_samples = 4.


100%|██████████| 35/35 [00:00<00:00, 47.19it/s]


VotingRegressor model failed to execute
VotingRegressor.__init__() missing 1 required positional argument: 'estimators'
-----------------------------------------------------
year 2021
-----------------------------------------------------
-----------------------------------------------------
year 2022
-----------------------------------------------------
-----------------------------------------------------
year 2023
-----------------------------------------------------


In [7]:
# ------------------------------------- GridSearchCV

# Importation des librairies
import pandas as pd
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import (
    HistGradientBoostingRegressor,
    GradientBoostingRegressor,
    RandomForestRegressor,
    BaggingRegressor,
    AdaBoostRegressor,
)
from sklearn.tree import DecisionTreeRegressor, ExtraTreeRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.linear_model import (
    PoissonRegressor,
    Lars,
    LarsCV,
    LinearRegression,
    Ridge,
    RidgeCV,
    BayesianRidge,
    LassoLarsIC,
    LassoCV,
    LassoLarsCV,
    ElasticNetCV,
    OrthogonalMatchingPursuitCV,
    PassiveAggressiveRegressor,
    RANSACRegressor,
    SGDRegressor,
    HuberRegressor,
    TheilSenRegressor,
    ElasticNet,
    OrthogonalMatchingPursuit,
    LassoLars,
    Lasso,
)
from sklearn.svm import LinearSVR
from sklearn.cross_decomposition import PLSRegression
from sklearn.neighbors import KNeighborsRegressor
from sklearn.compose import TransformedTargetRegressor

from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split, KFold

from sklearn.metrics import (
    accuracy_score,
    root_mean_squared_error,
    mean_absolute_error,
    r2_score,
)


# Hyperparamètres larges pour chaque modèle
param_grid = {
    # "HistGradientBoostingRegressor": {
    #     "learning_rate": [0.01, 0.05, 0.1],
    #     "max_iter": [100, 200, 300],
    #     "max_depth": [None, 5, 10, 15, 20],
    # },
    "HistGradientBoostingRegressor": {
        "learning_rate": [0.05, 0.1],
        "max_iter": [100, 300],
        "max_depth": [None, 15, 20],
    },
    # "MLPRegressor": {
    #     "hidden_layer_sizes": [(50,), (100,), (50, 50), (100, 100)],
    #     "activation": ["relu", "tanh", "logistic"],
    #     # "solver": ["adam", "sgd"],
    #     "learning_rate_init": [0.001, 0.01, 0.1],
    # },
    "MLPRegressor": {
        "hidden_layer_sizes": [(50, 50), (100, 100)],
        "activation": ["tanh", "logistic"],
        "learning_rate_init": [0.001, 0.01],
    },
    # "GradientBoostingRegressor": {
    #     "learning_rate": [0.01, 0.1, 0.2],
    #     "n_estimators": [100, 200, 300],
    #     "max_depth": [3, 5, 7],
    # },
    "GradientBoostingRegressor": {
        "learning_rate": [0.01, 0.1, 0.2],
        "n_estimators": [100, 200],
        "max_depth": [7, 10],
    },
    "DecisionTreeRegressor": {
        "max_depth": [None, 10, 20, 30],
        "min_samples_split": [2, 5, 10],
        "min_samples_leaf": [1, 2, 4],
    },
    "ExtraTreeRegressor": {
        "max_depth": [None, 10, 20, 30],
        "min_samples_split": [2, 5, 10],
        "min_samples_leaf": [1, 2, 4],
    },
    "RandomForestRegressor": {
        "n_estimators": [100, 200, 300],
        "max_depth": [None, 10, 20, 30],
        # "min_samples_split": [2, 5, 10],
    },
    "BaggingRegressor": {
        "n_estimators": [10, 50, 100],
        "max_samples": [0.5, 0.75, 1.0],
        "max_features": [0.5, 1.0],
    },
    "AdaBoostRegressor": {
        "n_estimators": [50, 100, 200],
        "learning_rate": [0.1, 0.5, 1.0],
    },
    "PoissonRegressor": {
        "alpha": [0.01, 0.1, 1.0],
    },
    "Lars": {
        "n_nonzero_coefs": [1, 5, 10, 20],
    },
    "LinearRegression": {},
    "TransformedTargetRegressor": {},
    "Ridge": {
        "alpha": [-5, 0.1, 1.0, 10.0, 50.0, 100.0],
        "fit_intercept": [True, False],
    },
    "BayesianRidge": {
        "alpha_1": [1e-6, 1e-5, 1e-4],
        "alpha_2": [1e-6, 1e-5, 1e-4],
    },
    "LassoLarsIC": {"criterion": ["aic", "bic"]},
    "OrthogonalMatchingPursuitCV": {},
    "PLSRegression": {
        "n_components": [2, 5, 10],
    },
    "TheilSenRegressor": {
        "max_subpopulation": [10000, 100000],
    },
    "HuberRegressor": {
        "alpha": [0.01, 0.1, 1.0],
    },
    "LinearSVR": {
        "C": [0.1, 1.0, 10.0],
        "epsilon": [0.1, 0.2, 0.3],
    },
    "Lasso": {
        "alpha": [0.1, 1.0, 5.0, 10.0],
    },
    "ElasticNet": {
        "alpha": [0.1, 1.0, 10.0],
        "l1_ratio": [0.1, 0.5, 0.7, 0.9],
    },
    "OrthogonalMatchingPursuit": {},
    "KNeighborsRegressor": {
        "n_neighbors": [3, 5, 10, 15],
        "weights": ["uniform", "distance"],
    },
    "PassiveAggressiveRegressor": {
        "C": [0.1, 1.0, 10.0],
    },
    "RANSACRegressor": {"min_samples": [0.1, 0.5, 0.75], "max_trials": [100, 200, 300]},
    "SGDRegressor": {
        "alpha": [0.0001, 0.001, 0.01],
        "penalty": ["l2", "l1", "elasticnet"],
    },
}

# Liste des modèles
regressors = {
    "HistGradientBoostingRegressor": HistGradientBoostingRegressor(),
    "MLPRegressor": MLPRegressor(),
    "GradientBoostingRegressor": GradientBoostingRegressor(),
    "DecisionTreeRegressor": DecisionTreeRegressor(),
    "ExtraTreeRegressor": ExtraTreeRegressor(),
    "RandomForestRegressor": RandomForestRegressor(),
    "BaggingRegressor": BaggingRegressor(),
    "AdaBoostRegressor": AdaBoostRegressor(),
    # "PoissonRegressor": PoissonRegressor(),
    # "Lars": Lars(),
    # "LinearRegression": LinearRegression(),
    # "TransformedTargetRegressor": TransformedTargetRegressor(
    #     regressor=LinearRegression()
    # ),
    # "Ridge": Ridge(),
    # "BayesianRidge": BayesianRidge(),
    # "LassoLarsIC": LassoLarsIC(),
    # "OrthogonalMatchingPursuitCV": OrthogonalMatchingPursuitCV(),
    # "PLSRegression": PLSRegression(),
    # "TheilSenRegressor": TheilSenRegressor(),
    # "HuberRegressor": HuberRegressor(),
    # "LinearSVR": LinearSVR(),
    # "LassoLars": LassoLars(),
    # "Lasso": Lasso(),
    # "ElasticNet": ElasticNet(),
    # "OrthogonalMatchingPursuit": OrthogonalMatchingPursuit(),
    # "KNeighborsRegressor": KNeighborsRegressor(),
    # "PassiveAggressiveRegressor": PassiveAggressiveRegressor(),
    # "RANSACRegressor": RANSACRegressor(),
    # "SGDRegressor": SGDRegressor(),
}

cols_cible_filter = [
    "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    "PumpSecondsOnSite_mean",
]

results = []
crossval = KFold(n_splits=5, random_state=42, shuffle=True)

# 
for index, name in enumerate(cols_cible_type):
    df = load_df(name)

    for year_floor in range(14, 15):  # >= 2022
        print("-----------------------------------------------------")
        print("year", 2024 - 16 + year_floor)
        print("-----------------------------------------------------")
        df_limited = df[df.CalYear >= year_floor]  
        X = Create_X(df_limited, index)
        for index_cible, col_cible in enumerate(cols_cible[index]):
            if not (col_cible in cols_cible_filter):
                continue
            print(
                "--------------------------------------------------------------------------------"
            )
            print("///////////////////////////", "cible", col_cible)
            y = df_limited[col_cible]
            X_train, X_test, y_train, y_test = train_test_split(
                X, y, test_size=0.2, random_state=42
            )
            # Réchantillonne
            # X_train_smote, y_train_smote = under_sampling(X_train, y_train)
            X_train_samp = X_train
            y_train_samp = y_train

            # Exécuter GridSearchCV pour chaque modèle
            for model_name, model in regressors.items():
                # Controle run, car potentiellement long
                print("-------------------------------------------")
                print(f"GridSearchCV pour {model_name}")
                grid = GridSearchCV(
                    model,
                    param_grid[model_name],
                    scoring="neg_mean_squared_error",
                    cv=crossval,
                    n_jobs=2, #-1,
                    verbose=2,
                )
                # Fit et Predict
                grid.fit(X_train_samp, y_train_samp)
                y_pred = grid.best_estimator_.predict(X_test)
                y_train_pred = grid.best_estimator_.predict(X_train_samp)
                # Meilleur score et meilleurs hyperparamètres
                best_params = grid.best_params_
                best_score = grid.best_score_
                # affiche de suite les résultat
                print(f"Meilleurs paramètres {best_params}")
                print(f"Meilleur score {best_score}")
                # R²
                train_r2 = r2_score(y_train_samp, y_train_pred)
                print(f"R² train : {train_r2}")
                test_r2 = r2_score(y_test, y_pred)
                print(f"R² test : {test_r2}")
                # train et test RMSE
                score_train = grid.score(X_train_samp, y_train_samp)
                print(f"Score train : {score_train}")
                score_test = grid.score(X_test, y_test)
                print(f"Score test : {score_test}")
                # RMSE
                rmse_train = root_mean_squared_error(y_train_samp, y_train_pred)
                print(f"RMSE train : {rmse_train}")
                rmse_test = root_mean_squared_error(y_test, y_pred)
                print(f"RMSE test : {rmse_test}")
                # MAE
                mae_train = mean_absolute_error(y_train_samp, y_train_pred)
                print(f"MAE train : {mae_train}")
                mae_test = mean_absolute_error(y_test, y_pred)
                print(f"MAE test : {mae_test}")

                # Score de validation croisée
                #             scores = cross_validate(grid, X_train, y_train, cv=crossval, scoring=['accuracy', 'precision', 'recall', 'f1'])
                #             cv_test_accuracy = f" cv_test_accuracy : {scores['test_accuracy'].mean()} (+/-{scores['test_accuracy'].std()})"
                #             cv_test_precision
                #             cv_test_recall
                #             cv_test_f1

                # {'fit_time': array([1.7602632 , 1.3521595 , 1.53327417, 1.6628437 , 1.52980328]),
                #  'score_time': array([0.10070086, 0.10009599, 0.11566949, 0.09443331, 0.09455991]),
                #  'test_accuracy': array([0.87765306, 0.87768222, 0.8774344 , 0.87757839, 0.87759297]),
                #  'test_precision': array([0.36      , 0.43243243, 0.2745098 , 0.29032258, 0.38888889]),
                #  'test_recall': array([0.00107322, 0.00190794, 0.00166965, 0.00107335, 0.00250447]),
                #  'test_f1': array([0.00214005, 0.00379912, 0.00331911, 0.00213878, 0.00497689])}

                # print("[StackingClassifier]: \n Accuracy: %0.2f (+/- %0.2f)\n" % (scores['test_accuracy'].mean(), scores['test_accuracy'].std()),
                #       "F1 score: %0.2f (+/- %0.2f)" % (scores['test_f1'].mean(), scores['test_f1'].std()))
                # >>>
                # [StackingClassifier]:
                #  Accuracy: 0.76 (+/- 0.02)
                #  F1 score: 0.62 (+/- 0.04)

                # Ajouter au tableau des résultats
                results.append(
                    {
                        "Target": col_cible,
                        "Year floor": 2024 - 16 + year_floor,
                        "Model": model_name,
                        "Best Params": best_params,
                        "Best Score": best_score,
                        "R-Squared train": train_r2,
                        "R-Squared test": test_r2,
                        "Score Train": score_train,
                        "Score Test": score_test,
                        "RMSE train": rmse_train,
                        "RMSE test": rmse_test,
                        "MAE train": mae_train,
                        "MAE test": mae_test,
                    }
                )
                df_results = pd.DataFrame(results)
                df_results = df_results.sort_values(by=["Target", "MAE test"], ascending=[False, True])
                df_results.to_csv(f"../data/_GridSearch_regressor.csv", sep=";", index=False)

print(results)
df_results = pd.DataFrame(results)
df_results = df_results.sort_values(by=["Target", "MAE test"], ascending=[False, True])
df_results.to_csv(f"../data/_GridSearch_regressor.csv", sep=";", index=False)

# p = plt.figure(figsize=(18,12))
# p = sns.set_theme(style="white")
# p = models=models.sort_values(by='Model Accuracy with GridSearch',ascending=False)
# p = sns.barplot(y= 'Model', x= 'Model Accuracy with GridSearch', data= models)
# for container in p.containers:
#     p.bar_label(container,label_type = 'edge',padding = 8,size = 20,color = "black",rotation = 0,
#     bbox={"boxstyle": "round", "pad": 0.6, "facecolor": "pink", "edgecolor": "Blue", "alpha": 1})
# plt.title('COMPARE THE MODEL')
# plt.xlabel('MODEL')
# plt.ylabel('Model Accuracy')
# plt.show()

-----------------------------------------------------
year 2022
-----------------------------------------------------
(342634, 42)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Postcode_district_0', 'Postcode_district_1', 'Postcode_district_2', 'Postcode_district_3', 'Postcode_district_4', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1248893       14             0             0             0             0   
1248894       14             0             0             0             0   

         HourOfCall_4  Postcode_district_0  Postcode_district_1  \
1248893             1                    0                    0   
1248894             1                    0                    0   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1248893                    0                    0                    1   
1248894                    0                    0                    1   

         Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  \
1248893        0        0        0        1            0            1   
1248894        0        0        0        1            0            1   

         DayOfWeek_2  
1248893            1  
1248894            1

(342634, 18)
--------------------------------------------------------------------------------
/////////////////////////// cible TurnoutTimeSeconds_mean
-------------------------------------------
GridSearchCV pour HistGradientBoostingRegressor
Fitting 5 folds for each of 12 candidates, totalling 60 fits
Meilleurs paramètres {'learning_rate': 0.1, 'max_depth': 20, 'max_iter': 100}
Meilleur score -1166.7342407438052
R² train : 0.14646706102948992
R² test : 0.14815032430313346
Score train : -1161.4649969009824
Score test : -1182.4627398319167
RMSE train : 34.08027284076497
RMSE test : 34.386955954720925
MAE train : 21.87042208144383
MAE test : 21.941782470690125
-------------------------------------------
GridSearchCV pour MLPRegressor
Fitting 5 folds for each of 8 candidates, totalling 40 fits
Meilleurs paramètres {'activation': 'logistic', 'hidden_layer_sizes': (50, 50), 'learning_rate_init': 0.001}
Meilleur score -1169.6960919361677
R² train : 0.14280193966901067
R² test : 0.1450065205

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1248893       14             0             0             0             0   
1248894       14             0             0             0             0   

         HourOfCall_4  Postcode_district_0  Postcode_district_1  \
1248893             1                    0                    1   
1248894             1                    0                    1   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1248893                    0                    0                    0   
1248894                    0                    0                    0   

         Postcode_district_5  Postcode_district_6  Postcode_district_7  \
1248893                    0                    0                    0   
1248894                    1                    1                    0   

         Postcode_district_8  Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  \
1248893                    0        0        0        0        1            0   
1248894                    0        0        0        0        1            0   

         DayOfWeek_1  DayOfWeek_2  
1248893            1            1  
1248894            1            1

(342634, 22)
--------------------------------------------------------------------------------
/////////////////////////// cible TravelTimeSeconds_mean
-------------------------------------------
GridSearchCV pour HistGradientBoostingRegressor
Fitting 5 folds for each of 12 candidates, totalling 60 fits
Meilleurs paramètres {'learning_rate': 0.1, 'max_depth': 15, 'max_iter': 300}
Meilleur score -16454.018481412757
R² train : 0.12272014314634072
R² test : 0.11020176507988466
Score train : -16162.593937923179
Score test : -16350.480506384487
RMSE train : 127.13219080124112
RMSE test : 127.86899744028842
MAE train : 92.82680030437741
MAE test : 93.02890657947654
-------------------------------------------
GridSearchCV pour MLPRegressor
Fitting 5 folds for each of 8 candidates, totalling 40 fits
Meilleurs paramètres {'activation': 'logistic', 'hidden_layer_sizes': (50, 50), 'learning_rate_init': 0.001}
Meilleur score -16417.578655949823
R² train : 0.11958420598059272
R² test : 0.11081496835

CalYear  PropertyType_0  PropertyType_1  PropertyType_2  \
1248893       14               0               0               0   
1248894       14               0               1               1   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1248893               0               0               1               0   
1248894               1               1               0               0   

         StopCode_0  StopCode_1  StopCode_2  StopCode_3  StopCode_4  
1248893           0           0           0           1           1  
1248894           0           0           0           1           0

(342634, 13)
--------------------------------------------------------------------------------
/////////////////////////// cible PumpSecondsOnSite_mean
-------------------------------------------
GridSearchCV pour HistGradientBoostingRegressor
Fitting 5 folds for each of 12 candidates, totalling 60 fits
Meilleurs paramètres {'learning_rate': 0.1, 'max_depth': 15, 'max_iter': 100}
Meilleur score -1687085.1483349619
R² train : 0.2252070538581309
R² test : 0.22554083537116698
Score train : -1678649.350574539
Score test : -1673725.717708009
RMSE train : 1295.627010591605
RMSE test : 1293.7255186893428
MAE train : 705.2391789473915
MAE test : 710.1610297881622
-------------------------------------------
GridSearchCV pour MLPRegressor
Fitting 5 folds for each of 8 candidates, totalling 40 fits
Meilleurs paramètres {'activation': 'logistic', 'hidden_layer_sizes': (100, 100), 'learning_rate_init': 0.01}
Meilleur score -1689474.264508313
R² train : 0.22478965621924973
R² test : 0.224897263564103

In [10]:
# -------------------------------------------- XGBoost

import pandas as pd
import xgboost as xgb

from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split, KFold

# from xgboost import XGBRegressor
from xgboost import XGBRegressor

from tqdm import tqdm  # Pour la barre de progression
from sklearn.metrics import (
    accuracy_score,
    root_mean_squared_error,
    mean_absolute_error,
    r2_score,
)

# Hyperparamètres larges pour chaque modèle
# param_grid = {
#     "XGBoost": {
#         "n_estimators": [50, 100, 200],
#         "max_depth": [3, 5, 7],
#         "learning_rate": [0.01, 0.1, 0.2],
#         "subsample": [0.6, 0.8, 1.0],
#         "colsample_bytree": [0.6, 0.8, 1.0],
#     },
# }

# # Liste des modèles
# regressors = {
#     "XGBoost": XGBRegressor(objective="reg:squarederror", random_state=42),
# }

param_grid = {
    "n_estimators": [50, 100, 200],
    "max_depth": [3, 5, 7],
    "learning_rate": [0.01, 0.1, 0.2],
    "subsample": [0.6, 0.8, 1.0],
    "colsample_bytree": [0.6, 0.8, 1.0],
}

cols_cible_filter = [
    "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    "PumpSecondsOnSite_mean",
]

results = []
crossval = KFold(n_splits=5, random_state=42, shuffle=True)

total_combinations = (
    len(param_grid["n_estimators"])
    * len(param_grid["max_depth"])
    * len(param_grid["learning_rate"])
    * len(param_grid["subsample"])
    * len(param_grid["colsample_bytree"])
)

def do_test():
    with tqdm(total=total_combinations, desc="Optimisation") as pbar:
        # Itération sur les combinaisons d'hyperparamètres
        for n_estimators in param_grid["n_estimators"]:
            for max_depth in param_grid["max_depth"]:
                for learning_rate in param_grid["learning_rate"]:
                    for subsample in param_grid["subsample"]:
                        for colsample_bytree in param_grid["colsample_bytree"]:
                            train_rmse_scores = []
                            test_rmse_scores = []
                            train_mae_scores = []
                            test_mae_scores = []

                            # Itération sur les splits de KFold
                            for train_index, test_index in crossval.split(X):
                                X_train, X_test = (
                                    X.iloc[train_index],
                                    X.iloc[test_index],
                                )
                                y_train, y_test = (
                                    y.iloc[train_index],
                                    y.iloc[test_index],
                                )

                                # Initialisation du modèle avec GPU
                                model = XGBRegressor(
                                    n_estimators=n_estimators,
                                    max_depth=max_depth,
                                    learning_rate=learning_rate,
                                    subsample=subsample,
                                    colsample_bytree=colsample_bytree,
                                    tree_method="gpu_hist",  # Utiliser le GPU
                                    random_state=42,
                                )

                                # Entraînement du modèle
                                model.fit(X_train, y_train)

                                # Prédictions
                                y_train_pred = model.predict(X_train)
                                y_test_pred = model.predict(X_test)

                                # Calcul des métriques
                                train_rmse_scores.append(
                                    root_mean_squared_error(y_train, y_train_pred)
                                )
                                test_rmse_scores.append(
                                    root_mean_squared_error(y_test, y_test_pred)
                                )
                                train_mae_scores.append(
                                    mean_absolute_error(y_train, y_train_pred)
                                )
                                test_mae_scores.append(
                                    mean_absolute_error(y_test, y_test_pred)
                                )
                            # print(
                            #     "train_mae",
                            #     np.mean(train_mae_scores),
                            #     "test_mae",
                            #     np.mean(test_mae_scores),
                            # )
                            # Moyenne des scores pour cette combinaison d'hyperparamètres
                            results.append(
                                {
                                    "Target": col_cible,
                                    "Year floor": 2024 - 16 + year_floor,
                                    "n_estimators": n_estimators,
                                    "max_depth": max_depth,
                                    "learning_rate": learning_rate,
                                    "subsample": subsample,
                                    "colsample_bytree": colsample_bytree,
                                    "train_rmse": np.mean(train_rmse_scores),
                                    "test_rmse": np.mean(test_rmse_scores),
                                    "train_mae": np.mean(train_mae_scores),
                                    "test_mae": np.mean(test_mae_scores),
                                }
                            )

                            df_results = pd.DataFrame(results)
                            df_results = df_results.sort_values(
                                by=["Target", "test_mae"], ascending=[False, True]
                            )
                            df_results.to_csv(
                                f"../data/_GridSearch_XGBoost_regressor.csv",
                                sep=";",
                                index=False,
                            )
                            # Mettre à jour la barre de progression
                            pbar.update(1)


for index, name in enumerate(cols_cible_type):
    df = load_df(name)

    for year_floor in range(14, 15):  # >= 2022
        print("-----------------------------------------------------")
        print("year", 2024 - 16 + year_floor)
        print("-----------------------------------------------------")
        df_limited = df[df.CalYear >= year_floor]
        X = Create_X(df_limited, index)
        for index_cible, col_cible in enumerate(cols_cible[index]):
            if not (col_cible in cols_cible_filter):
                continue
            print(
                "--------------------------------------------------------------------------------"
            )
            print("///////////////////////////", "cible", col_cible)
            y = df_limited[col_cible]
            do_test()

print(results)
df_results = pd.DataFrame(results)
df_results = df_results.sort_values(by=["Target", "test_mae"], ascending=[False, True])
df_results.to_csv(f"../data/_GridSearch_XGBoost_regressor.csv", sep=";", index=False)

-----------------------------------------------------
year 2022
-----------------------------------------------------
(342634, 42)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Postcode_district_0', 'Postcode_district_1', 'Postcode_district_2', 'Postcode_district_3', 'Postcode_district_4', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1248893       14             0             0             0             0   
1248894       14             0             0             0             0   

         HourOfCall_4  Postcode_district_0  Postcode_district_1  \
1248893             1                    0                    0   
1248894             1                    0                    0   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1248893                    0                    0                    1   
1248894                    0                    0                    1   

         Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  \
1248893        0        0        0        1            0            1   
1248894        0        0        0        1            0            1   

         DayOfWeek_2  
1248893            1  
1248894            1

(342634, 18)
--------------------------------------------------------------------------------
/////////////////////////// cible TurnoutTimeSeconds_mean


Optimisation: 100%|██████████| 243/243 [16:45<00:00,  4.14s/it]


-----------------------------------------------------
year 2022
-----------------------------------------------------
(342634, 45)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Postcode_district_0', 'Postcode_district_1', 'Postcode_district_2', 'Postcode_district_3', 'Postcode_district_4', 'Postcode_district_5', 'Postcode_district_6', 'Postcode_district_7', 'Postcode_district_8', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


...

-----------------------------------------------------
year 2022
-----------------------------------------------------
(342634, 40)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'PropertyType_0', 'PropertyType_1', 'PropertyType_2', 'PropertyType_3', 'PropertyType_4', 'PropertyType_5', 'PropertyType_6', 'StopCode_0', 'StopCode_1', 'StopCode_2', 'StopCode_3', 'StopCode_4']


CalYear  PropertyType_0  PropertyType_1  PropertyType_2  \
1248893       14               0               0               0   
1248894       14               0               1               1   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1248893               0               0               1               0   
1248894               1               1               0               0   

         StopCode_0  StopCode_1  StopCode_2  StopCode_3  StopCode_4  
1248893           0           0           0           1           1  
1248894           0           0           0           1           0

(342634, 13)
--------------------------------------------------------------------------------
/////////////////////////// cible PumpSecondsOnSite_mean


Optimisation: 100%|██████████| 243/243 [15:27<00:00,  3.82s/it]

[{'Target': 'TurnoutTimeSeconds_mean', 'Year floor': 2022, 'n_estimators': 50, 'max_depth': 3, 'learning_rate': 0.01, 'subsample': 0.6, 'colsample_bytree': 0.6, 'train_rmse': np.float64(36.11794695460797), 'test_rmse': np.float64(36.1168811335287), 'train_mae': np.float64(24.029191574678883), 'test_mae': np.float64(24.029871732194216)}, {'Target': 'TurnoutTimeSeconds_mean', 'Year floor': 2022, 'n_estimators': 50, 'max_depth': 3, 'learning_rate': 0.01, 'subsample': 0.6, 'colsample_bytree': 0.8, 'train_rmse': np.float64(35.77113362348869), 'test_rmse': np.float64(35.769818588599776), 'train_mae': np.float64(23.652761375204378), 'test_mae': np.float64(23.653317375953815)}, {'Target': 'TurnoutTimeSeconds_mean', 'Year floor': 2022, 'n_estimators': 50, 'max_depth': 3, 'learning_rate': 0.01, 'subsample': 0.6, 'colsample_bytree': 1.0, 'train_rmse': np.float64(35.38120491162341), 'test_rmse': np.float64(35.379678623597414), 'train_mae': np.float64(23.217412753182945), 'test_mae': np.float64(23.

In [4]:
# --------------------------------------- Voting et Stacking

import pandas as pd

from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split, KFold
from sklearn.ensemble import VotingRegressor, StackingRegressor
from xgboost import XGBRegressor


from sklearn.ensemble import (
    HistGradientBoostingRegressor,
    GradientBoostingRegressor,
    RandomForestRegressor,
)
from sklearn.tree import ExtraTreeRegressor
from sklearn.neural_network import MLPRegressor

from sklearn.metrics import (
    root_mean_squared_error,
    mean_absolute_error,
    r2_score,
)


def get_estimators(index):

    """
    Cette fonction retourne une liste de modèles de régression prédéfinis (estimators) en fonction de l'index fourni.
    
    Arguments:
    index (int) : L'index de la liste d'estimateurs à retourner. 
                  
    
    Retourne:
    list : Liste de tuples, où chaque tuple contient :
           - Le nom du modèle .
           - L'instance du modèle avec ses hyperparamètres associés.
           
    Exemple d'utilisation:
    >>> get_estimators(0)   # Retourne la première liste de modèles avec hyperparamètres spécifiques
    >>> get_estimators(1)   # Retourne la deuxième liste de modèles avec des configurations ajustées
    >>> get_estimators(2)   # Retourne la troisième liste de modèles avec d'autres options
    

    """

    if index == 0:
        return [
            (
                "XGBRegressor",
                XGBRegressor(
                    n_estimators=100,
                    max_depth=5,
                    learning_rate=0.1,
                    subsample=1.0,
                    colsample_bytree=0.8,
                ),
            ),
            (
                "HistGradientBoostingRegressor",
                HistGradientBoostingRegressor(
                    learning_rate=0.1, max_depth=20, max_iter=100
                ),
            ),
            (
                "GradientBoostingRegressor",
                GradientBoostingRegressor(
                    learning_rate=0.1, max_depth=7, n_estimators=100
                ),
            ),
            (
                "RandomForestRegressor",
                RandomForestRegressor(max_depth=10, n_estimators=300),
            ),
            (
                "MLPRegressor",
                MLPRegressor(
                    activation="logistic",
                    hidden_layer_sizes=(50, 50),
                    learning_rate_init=0.001,
                ),
            ),
        ]
    elif index == 1:
        return [
            (
                "XGBRegressor",
                XGBRegressor(
                    n_estimators=200,
                    max_depth=7,
                    learning_rate=0.1,
                    subsample=1.0,
                    colsample_bytree=0.8,
                ),
            ),
            (
                "GradientBoostingRegressor",
                GradientBoostingRegressor(
                    learning_rate=0.1, max_depth=7, n_estimators=200
                ),
            ),
            (
                "HistGradientBoostingRegressor",
                HistGradientBoostingRegressor(
                    learning_rate=0.1, max_depth=15, max_iter=300
                ),
            ),
            (
                "MLPRegressor",
                MLPRegressor(
                    activation="logistic",
                    hidden_layer_sizes=(50, 50),
                    learning_rate_init=0.001,
                ),
            ),
            (
                "RandomForestRegressor",
                RandomForestRegressor(max_depth=10, n_estimators=200),
            ),
        ]
    else:
        return [
            (
                "XGBRegressor",
                XGBRegressor(
                    n_estimators=100,
                    max_depth=7,
                    learning_rate=0.1,
                    subsample=1.0,
                    colsample_bytree=0.8,
                ),
            ),
            (
                "MLPRegressor",
                MLPRegressor(
                    activation="logistic",
                    hidden_layer_sizes=(100, 100),
                    learning_rate_init=0.01,
                ),
            ),
            (
                "HistGradientBoostingRegressor",
                HistGradientBoostingRegressor(
                    learning_rate=0.1, max_depth=15, max_iter=100
                ),
            ),
            (
                "ExtraTreeRegressor",
                ExtraTreeRegressor(
                    max_depth=10, min_samples_leaf=4, min_samples_split=10
                ),
            ),
            (
                "RandomForestRegressor",
                RandomForestRegressor(max_depth=10, n_estimators=300),
            ),
        ]


cols_cible_filter = [
    "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    "PumpSecondsOnSite_mean",
]

regressors = [
    {
        "VotingRegressor": VotingRegressor(estimators=get_estimators(0)),
        "StackingRegressor": StackingRegressor(estimators=get_estimators(0)),
    },
    {
        "VotingRegressor": VotingRegressor(estimators=get_estimators(1)),
        "StackingRegressor": StackingRegressor(estimators=get_estimators(1)),
    },
    {
        "VotingRegressor": VotingRegressor(estimators=get_estimators(2)),
        "StackingRegressor": StackingRegressor(estimators=get_estimators(2)),
    },
]

results = []
crossval = KFold(n_splits=5, random_state=42, shuffle=True)

for index, name in enumerate(cols_cible_type):
    df = load_df(name)

    for year_floor in range(14, 15):  # >= 2022
        print("-----------------------------------------------------")
        print("year", 2024 - 16 + year_floor)
        print("-----------------------------------------------------")
        df_limited = df[df.CalYear >= year_floor]
        X = Create_X(df_limited, index)
        for index_cible, col_cible in enumerate(cols_cible[index]):
            if not (col_cible in cols_cible_filter):
                continue
            print(
                "--------------------------------------------------------------------------------"
            )
            print("///////////////////////////", "cible", col_cible)
            y = df_limited[col_cible]
            X_train, X_test, y_train, y_test = train_test_split(
                X, y, test_size=0.2, random_state=42
            )
            # Réchantillonne
            # X_train_smote, y_train_smote = under_sampling(X_train, y_train)
            X_train_samp = X_train
            y_train_samp = y_train

            # Exécuter GridSearchCV pour chaque modèle
            for model_name, model in regressors[index].items():
                # Controle run, car potentiellement long
                print("-------------------------------------------")
                print(f"Model pour {model_name}")
                # Fit et Predict
                model.fit(X_train_samp, y_train_samp)
                y_pred = model.predict(X_test)
                y_train_pred = model.predict(X_train_samp)
                # R²
                train_r2 = r2_score(y_train_samp, y_train_pred)
                print(f"R² train : {train_r2}")
                test_r2 = r2_score(y_test, y_pred)
                print(f"R² test : {test_r2}")
                # RMSE
                rmse_train = root_mean_squared_error(y_train_samp, y_train_pred)
                print(f"RMSE train : {rmse_train}")
                rmse_test = root_mean_squared_error(y_test, y_pred)
                print(f"RMSE test : {rmse_test}")
                # MAE
                mae_train = mean_absolute_error(y_train_samp, y_train_pred)
                print(f"MAE train : {mae_train}")
                mae_test = mean_absolute_error(y_test, y_pred)
                print(f"MAE test : {mae_test}")

                # Ajouter au tableau des résultats
                results.append(
                    {
                        "Target": col_cible,
                        "Year floor": 2024 - 16 + year_floor,
                        "Model": model_name,
                        "R-Squared train": train_r2,
                        "R-Squared test": test_r2,
                        "RMSE train": rmse_train,
                        "RMSE test": rmse_test,
                        "MAE train": mae_train,
                        "MAE test": mae_test,
                    }
                )
                df_results = pd.DataFrame(results)
                df_results = df_results.sort_values(
                    by=["Target", "MAE test"], ascending=[False, True]
                )
                df_results.to_csv(
                    f"../data/_VotingStacking_regressor.csv", sep=";", index=False
                )

print(results)
df_results = pd.DataFrame(results)
df_results = df_results.sort_values(by=["Target", "MAE test"], ascending=[False, True])
df_results.to_csv(f"../data/_VotingStacking_regressor.csv", sep=";", index=False)

-----------------------------------------------------
year 2022
-----------------------------------------------------
(342634, 42)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Postcode_district_0', 'Postcode_district_1', 'Postcode_district_2', 'Postcode_district_3', 'Postcode_district_4', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1248893       14             0             0             0             0   
1248894       14             0             0             0             0   

         HourOfCall_4  Postcode_district_0  Postcode_district_1  \
1248893             1                    0                    0   
1248894             1                    0                    0   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1248893                    0                    0                    1   
1248894                    0                    0                    1   

         Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  \
1248893        0        0        0        1            0            1   
1248894        0        0        0        1            0            1   

         DayOfWeek_2  
1248893            1  
1248894            1

(342634, 18)
--------------------------------------------------------------------------------
/////////////////////////// cible TurnoutTimeSeconds_mean
-------------------------------------------
Model pour VotingRegressor
R² train : 0.14704373838971685
R² test : 0.14709222520662935
RMSE train : 34.06875797026396
RMSE test : 34.40830568138454
MAE train : 21.84487880609663
MAE test : 21.938449743516383
-------------------------------------------
Model pour StackingRegressor
R² train : 0.1481004448257931
R² test : 0.14779618840499853
RMSE train : 34.047647958862335
RMSE test : 34.394102984590226
MAE train : 21.86219555265019
MAE test : 21.94969906625755
-----------------------------------------------------
year 2022
-----------------------------------------------------
(342634, 45)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsO

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1248893       14             0             0             0             0   
1248894       14             0             0             0             0   

         HourOfCall_4  Postcode_district_0  Postcode_district_1  \
1248893             1                    0                    1   
1248894             1                    0                    1   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1248893                    0                    0                    0   
1248894                    0                    0                    0   

         Postcode_district_5  Postcode_district_6  Postcode_district_7  \
1248893                    0                    0                    0   
1248894                    1                    1                    0   

         Postcode_district_8  Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  \
1248893                    0        0        0        0        1            0   
1248894                    0        0        0        0        1            0   

         DayOfWeek_1  DayOfWeek_2  
1248893            1            1  
1248894            1            1

(342634, 22)
--------------------------------------------------------------------------------
/////////////////////////// cible TravelTimeSeconds_mean
-------------------------------------------
Model pour VotingRegressor
R² train : 0.1356019609424901
R² test : 0.11533321874750768
RMSE train : 126.19534598921541
RMSE test : 127.49975497878333
MAE train : 92.07650755617546
MAE test : 92.72628338202044
-------------------------------------------
Model pour StackingRegressor
R² train : 0.13439175919746815
R² test : 0.11699949361416973
RMSE train : 126.28365508052144
RMSE test : 127.37962513239663
MAE train : 92.02616987903964
MAE test : 92.52171549276018
-----------------------------------------------------
year 2022
-----------------------------------------------------
(342634, 40)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsO

CalYear  PropertyType_0  PropertyType_1  PropertyType_2  \
1248893       14               0               0               0   
1248894       14               0               1               1   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1248893               0               0               1               0   
1248894               1               1               0               0   

         StopCode_0  StopCode_1  StopCode_2  StopCode_3  StopCode_4  
1248893           0           0           0           1           1  
1248894           0           0           0           1           0

(342634, 13)
--------------------------------------------------------------------------------
/////////////////////////// cible PumpSecondsOnSite_mean
-------------------------------------------
Model pour VotingRegressor
R² train : 0.22909965099007013
R² test : 0.22640325385381754
RMSE train : 1292.3682661188725
RMSE test : 1293.004987746
MAE train : 704.1935130260296
MAE test : 710.3881127276229
-------------------------------------------
Model pour StackingRegressor
R² train : 0.22637959964059173
R² test : 0.22513827158984434
RMSE train : 1294.646260057132
RMSE test : 1294.061714191511
MAE train : 702.6622667724416
MAE test : 707.9912317681343
[{'Target': 'TurnoutTimeSeconds_mean', 'Year floor': 2022, 'Model': 'VotingRegressor', 'R-Squared train': 0.14704373838971685, 'R-Squared test': 0.14709222520662935, 'RMSE train': np.float64(34.06875797026396), 'RMSE test': np.float64(34.40830568138454), 'MAE train': np.float64(21.84487880609663), 'MAE test': np.float64(21.938449743516383)}, {